In [192]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Import libraries

In [193]:
import sys
sys.path.append('..')

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import dartwork_mpl as dm

from scipy.stats import gaussian_kde
from matplotlib.ticker import MultipleLocator

# Figure 1.Grids

In [194]:
def make_points(n):
    """
    Point generator.
    """
    if n == 1:
        return np.array([0]), np.array([0])
    
    x = np.linspace(-2 * (n - 1), 2 * (n - 1), n)
    y = x

    x, y = np.meshgrid(x, y)

    return x, y

In [195]:
dm.use_dmpl_style()
plt.rcParams['font.size'] = 9

title_n = -1

fig = plt.figure(figsize=(dm.cm2in(15), dm.cm2in(15)))

offset = dm.make_offset(5, -5, fig)
offset2 = dm.make_offset(14, -5 + 0.5 * title_n, fig)

gs = fig.add_gridspec(
    2, 2, 
    left=0.1, right=0.95, bottom=0.1, top=0.95, 
    wspace=0.05, hspace=0.05,
)

axs = gs.subplots(sharex=True, sharey=True)

for n, ax, abc in zip((1, 2, 4, 8), axs.flat, 'abcd'):
    x, y = make_points(n)

    ax.scatter(x, y, s=9, c='dm.red5')
    ax.text(
        0, 1, f'{abc}', transform=ax.transAxes + offset, weight='bold',
        va='top', ha='left', fontsize=dm.fs(0),
    )

    ax.text(
        0, 1, f'{n} $\\times$ {n}', transform=ax.transAxes + offset2, weight='normal',
        va='top', ha='left', fontsize=dm.fs(title_n),
    )

for ax in axs.flat:
    ax.set_aspect(1)
    ax.set_xlim(-20, 20)
    ax.set_ylim(-20, 20)
    ax.set_xticks(np.arange(-18, 21, 4))
    ax.set_yticks(np.arange(-18, 21, 4))

    # 1 Minor tick between major ticks.
    ax.xaxis.set_minor_locator(MultipleLocator(2))
    ax.yaxis.set_minor_locator(MultipleLocator(2))
    
for ax in axs[:, 0]:
    ax.set_ylabel('$y$ coordinate [m]')

for ax in axs[1, :]:
    ax.set_xlabel('$x$ coordinate [m]')

dm.save_and_show(fig)

In [196]:
dm.save_formats(fig, './figure/Fig. 1. Grids')

# Figure 2. Parameter set

In [197]:
df = pd.read_csv('./data/fig2/parameter_set.csv')
df['Ground volumetric heat capacity'] /= 1e6
df['Borehole radius'] *= 100
df

BHE active length  Borehole radius  Ground thermal conductivity  \
0             99.001465         7.564697                     1.980299   
1             99.241699         7.564697                     1.980299   
2             99.001465         7.881104                     1.980299   
3             99.001465         7.564697                     2.077273   
4             99.001465         7.564697                     1.980299   
...                 ...              ...                          ...   
9795          99.537598         7.782959                     1.870962   
9796          99.537598         7.782959                     2.353154   
9797          99.537598         7.782959                     2.353154   
9798          99.537598         7.782959                     2.353154   
9799          99.537598         7.782959                     2.353154   

      Ground volumetric heat capacity  BHE distance  BHE buried depth  
0                            2.486816      4.022852          2.137695  
1                            2.486816      4.022852          2.137695  
2                            2.486816      4.022852          2.137695  
3                            2.486816      4.022852          2.137695  
4                            2.671387      4.022852          2.137695  
...                               ...           ...               ...  
9795                         2.643066      3.839258          1.911133  
9796                         2.142090      3.839258          1.911133  
9797                         2.643066      4.051367          1.911133  
9798                         2.643066      3.839258          2.152930  
9799                         2.643066      3.839258          1.911133  

[9800 rows x 6 columns]

In [198]:
columns = df.columns.to_list()
columns

['BHE active length',
 'Borehole radius',
 'Ground thermal conductivity',
 'Ground volumetric heat capacity',
 'BHE distance',
 'BHE buried depth']

In [199]:
dm.use_dmpl_style()
plt.rcParams['font.size'] = 9

name_dict = {
    'BHE active length' : '$L$ [m]',
    'Borehole radius' : '$r_b$ [cm]',
    'Ground thermal conductivity' : '$k_s$ [W/(m $\cdot$ K)]',
    'Ground volumetric heat capacity' : '$C_s$ [MJ/(m$^3$K)]', #10^6 으로 나눠서 사용하시면 됩니다. 
    'BHE distance' : '$d$ [m]',
    'BHE buried depth' : '$D$ [m]'
}

# None values are ignored.
range_info = {
    'BHE active length': {
        'lim': (99, 100),
        'ticks': (99.2, 99.8),
        'ticklabels': None,
    },
    'Borehole radius': {
        'lim': (7, 8.5),
        'ticks': (7.2, 8.3),
        'ticklabels': None,
    },
    'Ground thermal conductivity': {
        'lim': (1.5, 2.5),
        'ticks': (1.6, 2.4),
        'ticklabels': None,
    },
    'Ground volumetric heat capacity': {
        'lim': (2, 3),
        'ticks': (2.2, 2.8),
        'ticklabels': None,
    },
    'BHE distance': {
        'lim': (3.8, 4.2),
        'ticks': (3.9, 4.1),
        'ticklabels': None,
    },
    'BHE buried depth': {
        'lim': (1.8, 2.2),
        'ticks': (1.9, 2.1),
        'ticklabels': None,
    },
}


fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(17)))

gs = fig.add_gridspec(
    6, 6, left=0.1, right=0.95, bottom=0.1, top=0.95, wspace=0.2, hspace=0.2,    
)

axs = gs.subplots()


# Upper triangle is empty.
for r in range(6):
    for c in range(6):
        ax = axs[r, c]
        
        if r < c:
            ax.set_axis_off()

        if r == c:
            ax.yaxis.set_visible(False)


# Set y axis label.
for r, ax in enumerate(axs[:, 0]):
    ax.set_ylabel(name_dict[columns[r]])


# Set x axis label.
for c, ax in enumerate(axs[-1, :]):
    ax.set_xlabel(name_dict[columns[c]])


# Set diagonal spines.
# which one is the better? only bottom spine or all spines?
for i in range(6):
    # axs[i, i].spines['left'].set_visible(False)
    # axs[i, i].spines['top'].set_visible(False)
    # axs[i, i].spines['right'].set_visible(False)
    axs[i, i].spines['left'].set_visible(True)
    axs[i, i].spines['top'].set_visible(True)
    axs[i, i].spines['right'].set_visible(True)

# 1D histogram.
for i in range(6):
    axs[i, i].hist(df[columns[i]], bins=15, color='dm.red5', density=True, alpha=0.5)

# 2D histogram.
for r in range(6):
    for c in range(6):
        ax = axs[r, c]
        
        if r <= c:
            continue

        h, xedges, yedges = np.histogram2d(df[columns[c]], df[columns[r]], bins=15, density=True)

        X, Y = np.meshgrid(xedges, yedges)
        ax.pcolormesh(X, Y, h.T, cmap='Reds', alpha=0.7, vmax=(1.5 * h.max()))


# Set y axis range.
for r in range(6):
    name = columns[r]
    if name not in range_info:
        continue

    for c in range(r):
        ax = axs[r, c]
        # print(r, c)
        if range_info[name]['lim'] is not None:
            # print(name)
            ax.set_ylim(range_info[name]['lim'])

        if range_info[name]['ticks'] is not None:
            ax.set_yticks(range_info[name]['ticks'])

        if range_info[name]['ticklabels'] is not None:
            ax.set_yticklabels(range_info[name]['ticklabels'])

        if c != 0:
            ax.set_yticklabels([])


# Set x axis range.
for c in range(6):
    name = columns[c]
    if name not in range_info:
        continue

    for r in range(6):
        # print(r, c)

        ax = axs[r, c]
        
        if range_info[name]['lim'] is not None:
            # print(name)
            ax.set_xlim(range_info[name]['lim'])

        if range_info[name]['ticks'] is not None:
            ax.set_xticks(range_info[name]['ticks'])

        if range_info[name]['ticklabels'] is not None:
            ax.set_xticklabels(range_info[name]['ticklabels'])

        if r != (6 - 1):
            ax.set_xticklabels([])


# Remove grids.
for ax in axs.flat:
    ax.grid(False)


# Align y axis label.
fig.align_ylabels(axs[:, 0])

dm.save_and_show(fig)

In [200]:
dm.save_formats(fig, './figure/Fig. 2 Parameter sets generated using saltelli sampling')

The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.


# Figure 3. Temporal variation of g-function uncertainty

In [201]:
gval_data = {
    i: pd.read_csv(f'./data/fig3/gval_{i}x{i}.csv', index_col=0)
    for i in (1, 2, 4, 8)
}

gval_data[1]

1.0       2.0       3.0       4.0       5.0       7.0  \
Borefield_1     0.280342  0.522581  0.687601  0.811946  0.911584  1.065918   
Borefield_2     0.280342  0.522582  0.687602  0.811947  0.911586  1.065920   
Borefield_3     0.255991  0.491003  0.653165  0.775986  0.874677  1.027899   
Borefield_4     0.295017  0.541300  0.707899  0.833082  0.933238  1.088177   
Borefield_5     0.259015  0.494967  0.657506  0.780530  0.879350  1.032725   
...                  ...       ...       ...       ...       ...       ...   
Borefield_9796  0.229738  0.456149  0.614864  0.735839  0.833383  0.985258   
Borefield_9797  0.365747  0.628840  0.801878  0.930446  1.032686  1.190049   
Borefield_9798  0.297152  0.544002  0.710819  0.836116  0.936341  1.091359   
Borefield_9799  0.297152  0.544002  0.710819  0.836116  0.936341  1.091359   
Borefield_9800  0.297152  0.544002  0.710819  0.836116  0.936341  1.091359   

                     9.0      11.0      13.0      15.0  ...   81915.0  \
Borefield_1     1.183690  1.278918  1.358851  1.427723  ...  5.462624   
Borefield_2     1.183692  1.278922  1.358855  1.427728  ...  5.463224   
Borefield_3     1.145038  1.239859  1.319507  1.388169  ...  5.421286   
Borefield_4     1.206290  1.301738  1.381822  1.450805  ...  5.479905   
Borefield_5     1.149955  1.244836  1.324528  1.393224  ...  5.436457   
...                  ...       ...       ...       ...  ...       ...   
Borefield_9796  1.101636  1.195968  1.275278  1.343692  ...  5.388272   
Borefield_9797  1.309524  1.405838  1.486521  1.555939  ...  5.544262   
Borefield_9798  1.209515  1.304989  1.385090  1.454085  ...  5.471370   
Borefield_9799  1.209515  1.304989  1.385090  1.454085  ...  5.475670   
Borefield_9800  1.209515  1.304989  1.385090  1.454085  ...  5.471370   

                 98299.0  114683.0  131067.0  147451.0  163835.0  196603.0  \
Borefield_1     5.527670  5.580770  5.625269  5.663300  5.696301  5.751012   
Borefield_2     5.528327  5.581480  5.626029  5.664105  5.697149  5.751938   
Borefield_3     5.486302  5.539377  5.583855  5.621866  5.654851  5.709533   
Borefield_4     5.544329  5.596865  5.640846  5.678396  5.710947  5.764832   
Borefield_5     5.502409  5.556333  5.601589  5.640323  5.673983  5.729901   
...                  ...       ...       ...       ...       ...       ...   
Borefield_9796  5.454640  5.508956  5.554585  5.593675  5.627677  5.684239   
Borefield_9797  5.604743  5.653722  5.694449  5.728989  5.758738  5.807529   
Borefield_9798  5.534801  5.586453  5.629633  5.666450  5.698324  5.750988   
Borefield_9799  5.539378  5.591267  5.634653  5.671650  5.703685  5.756627   
Borefield_9800  5.534801  5.586453  5.629633  5.666450  5.698324  5.750988   

                229371.0  262139.0  294907.0  
Borefield_1     5.794759  5.830687  5.860794  
Borefield_2     5.795756  5.831750  5.861916  
Borefield_3     5.753257  5.789165  5.819256  
Borefield_4     5.807837  5.843090  5.872578  
Borefield_5     5.774737  5.811657  5.842674  
...                  ...       ...       ...  
Borefield_9796  5.729675  5.767156  5.798699  
Borefield_9797  5.845994  5.877164  5.902953  
Borefield_9798  5.792914  5.827202  5.855818  
Borefield_9799  5.798784  5.833270  5.862058  
Borefield_9800  5.792914  5.827202  5.855818  

[9800 rows x 79 columns]

In [202]:
def make_quntiles(data, n):
    x = data[n].columns.to_numpy().astype(float)
    # q = np.quantile(data[n].values, [0.025, 0.5, 0.975], axis=0)
    q = np.quantile(data[n].values, [0.0, 0.5, 1.0], axis=0)
    return x, q


x, q = make_quntiles(gval_data, 1)
q.shape

max_x = x.max()
max_x

294907.0

In [203]:
title_n = -1
label_n = 0

dm.use_dmpl_style()
plt.rcParams['font.size'] = 9

fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(13)))

offset = dm.make_offset(5, -5, fig)
offset2 = dm.make_offset(14, -5 + 0.5 * title_n, fig)

gs = fig.add_gridspec(
    2, 2, left=0.1, right=0.95, bottom=0.1, top=0.90, wspace=0.1, hspace=0.1,
)

axs = gs.subplots(sharex=True, sharey=True)

for n, ax, abc in zip((1, 2, 4, 8), axs.flat, 'abcd'):
    x, y = make_points(n)

    x, q = make_quntiles(gval_data, n)

    line, = ax.plot(x, q[1], c='dm.red7', lw=1.0)
    fill = ax.fill_between(x, q[0], q[2], color='dm.red5', alpha=0.25, lw=0)
    ax.text(
        0, 1, f'{abc}', transform=ax.transAxes + offset, weight='bold',
        va='top', ha='left', fontsize=dm.fs(0),
    )

    ax.text(
        0, 1, f'{n} $\\times$ {n}', transform=ax.transAxes + offset2, weight='normal',
        va='top', ha='left', fontsize=dm.fs(title_n),
    )

    if n == 2:
        ax.legend(
            [line, fill], 
            # ['Median', '95% credible interval'],
            ['Median', 'Uncertainty range'],
            loc='lower right', ncols=2, fontsize=dm.fs(label_n), bbox_to_anchor=(1.01, 1),
        )

for ax in axs.flat:
    ax.set_xlim(1, max_x)
    ax.set_ylim(0, 50)
    # ax.set_xticks(np.arange(label_n8, 21, 4))
    # ax.set_yticks(np.arange(-18, 21, 4))
    ax.set_xscale('log')
    
for ax in axs[:, 0]:
    ax.set_ylabel('g-function [-]')

for ax in axs[1, :]:
    ax.set_xlabel('Time [h]')

dm.save_and_show(fig)

In [204]:
dm.save_formats(fig, './figure/Fig. 3 Temporal variation of g-function uncertainty')

The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.


# Figure 4. Transient variation of the first order sensitivity index of parameters impact on g-function

In [205]:
sa_data = {
    i: pd.read_csv(f'./data/fig4_5/SA_{i}x{i}.csv', index_col=0).T
    for i in (1, 2, 4, 8)
}

sa_data[1]

BHE active length  Borehole radius  Ground thermal conductivity  \
1.0           -4.717437e-08         0.399644                     0.181658   
2.0           -7.069054e-08         0.400954                     0.182112   
3.0           -9.236880e-08         0.401318                     0.182217   
4.0           -1.123150e-07         0.401508                     0.182254   
5.0           -1.308513e-07         0.401636                     0.182268   
...                     ...              ...                          ...   
163835.0       1.532315e-04         0.644863                     0.110036   
196603.0       1.992050e-04         0.670893                     0.102171   
229371.0       2.471812e-04         0.694677                     0.094964   
262139.0       2.966019e-04         0.716515                     0.088327   
294907.0       3.469532e-04         0.736611                     0.082203   

          Ground volumetric heat capacity  BHE distance  BHE buried depth  
1.0                              0.431108           0.0     -7.130709e-17  
2.0                              0.429781           0.0     -1.102164e-16  
3.0                              0.429153           0.0     -3.249285e-16  
4.0                              0.428788           0.0      3.363617e-17  
5.0                              0.428544           0.0     -3.973285e-16  
...                                   ...           ...               ...  
163835.0                         0.254179           0.0      1.373954e-03  
196603.0                         0.235487           0.0      1.576063e-03  
229371.0                         0.218393           0.0      1.764700e-03  
262139.0                         0.202687           0.0      1.941593e-03  
294907.0                         0.188225           0.0      2.107906e-03  

[79 rows x 6 columns]

In [206]:
columns = sa_data[1].columns.to_list()
columns

['BHE active length',
 'Borehole radius',
 'Ground thermal conductivity',
 'Ground volumetric heat capacity',
 'BHE distance',
 'BHE buried depth']

In [207]:
dm.use_dmpl_style()
plt.rcParams['font.size'] = 9

cmap = plt.get_cmap('Set2')

name_dict = {
    'BHE active length' : '$L$ [m]',
    'Borehole radius' : '$r_b$ [cm]',
    'Ground thermal conductivity' : '$k_s$ [W/(m${\cdot}$K)]',
    'Ground volumetric heat capacity' : '$C_s$ [MJ/(m$^3$K)]', #10^6 으로 나눠서 사용하시면 됩니다. 
    'BHE distance' : '$d$ [m]',
    'BHE buried depth' : '$D$ [m]'
}

# 0의 값만 가지는 물성은 회색으로 처리.
colors = {
    'BHE active length' : 'dm.gray5',
    'Borehole radius' : cmap(0),
    'Ground thermal conductivity' : cmap(1),
    'Ground volumetric heat capacity' : cmap(2),
    'BHE distance' : cmap(3),
    'BHE buried depth' : 'dm.gray5'
}

lstyles =  {
    'BHE active length' : (0, (10, 3)),
    'Borehole radius' : '-',
    'Ground thermal conductivity' : '--',
    'Ground volumetric heat capacity' : ':',
    'BHE distance' : '-.',
    'BHE buried depth' : (0, (3, 5, 1, 5, 1, 5)),
}

lwidths = {
    'BHE active length' : 0.65,
    'Borehole radius' : 0.8,
    'Ground thermal conductivity' : 0.9,
    'Ground volumetric heat capacity' : 1.0,
    'BHE distance' : 0.85,
    'BHE buried depth' : 1.0,
}


fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(13)))

offset = dm.make_offset(5, -5, fig)
offset2 = dm.make_offset(14, -5 + 0.5 * title_n, fig)

gs = fig.add_gridspec(
    2, 2, left=0.1, right=0.95, bottom=0.1, top=0.90, wspace=0.1, hspace=0.15,
)

axs = gs.subplots(sharex=True, sharey=True)

lines = []
for n, ax, abc in zip((1, 2, 4, 8), axs.flat, 'abcd'):
    for name in columns:
        x = sa_data[n].index.to_numpy().astype(float)
        y = sa_data[n][name].to_numpy()

        line, = ax.plot(x, y, lw=lwidths[name], c=colors[name], ls=lstyles[name])
        lines.append(line)
    
    ax.text(
        0, 1, f'{abc}', transform=ax.transAxes + offset, weight='bold',
        va='top', ha='left', fontsize=dm.fs(0),
    )

    ax.text(
        0, 1, f'{n} $\\times$ {n}', transform=ax.transAxes + offset2, weight='normal',
        va='top', ha='left', fontsize=dm.fs(title_n),
    )

    if n == 1:
        ax.legend(
            lines[:3], [name_dict[name] for name in columns][:3],
            # loc='lower right', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(1.02, 1.02),
            mode='expand', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(0, 1.07, 1, 0.105),
            columnspacing=2.5,
        )

    if n == 2:
        ax.legend(
            lines[3:], [name_dict[name] for name in columns][3:],
            # loc='lower right', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(1.02, 1.02),
            mode='expand', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(0, 1.07, 1, 0.105),
            columnspacing=2.5,
        )

for ax in axs.flat:
    ax.set_xlim(1, max_x)
    ax.set_ylim(-0.03, 1)
    # ax.set_xticks(np.arange(-18, 21, 4))
    ax.set_yticks(np.arange(0, 1.1, 0.5))
    ax.set_xscale('log')
    
for ax in axs[:, 0]:
    # ax.set_ylabel('First-order sensitivity index')
    ax.set_ylabel('')

fig.text(0.025, 0.5, 'First-order sensitivity index [-]', va='center', rotation='vertical')

for ax in axs[1, :]:
    ax.set_xlabel('Time [h]')

dm.save_and_show(fig)

In [208]:
dm.save_formats(fig, './figure/Fig. 4 Transient variation of the first order sensitivity index of parameters impact on g-function')

# Figure 5. Transient variation of the first order sensitivity index of influential parameters on g-function

In [209]:
sa_data = {
    i: pd.read_csv(f'./data/fig4_5/SA_{i}x{i}.csv', index_col=0).T
    for i in (1, 2, 4, 8)
}

sa_data[1]

BHE active length  Borehole radius  Ground thermal conductivity  \
1.0           -4.717437e-08         0.399644                     0.181658   
2.0           -7.069054e-08         0.400954                     0.182112   
3.0           -9.236880e-08         0.401318                     0.182217   
4.0           -1.123150e-07         0.401508                     0.182254   
5.0           -1.308513e-07         0.401636                     0.182268   
...                     ...              ...                          ...   
163835.0       1.532315e-04         0.644863                     0.110036   
196603.0       1.992050e-04         0.670893                     0.102171   
229371.0       2.471812e-04         0.694677                     0.094964   
262139.0       2.966019e-04         0.716515                     0.088327   
294907.0       3.469532e-04         0.736611                     0.082203   

          Ground volumetric heat capacity  BHE distance  BHE buried depth  
1.0                              0.431108           0.0     -7.130709e-17  
2.0                              0.429781           0.0     -1.102164e-16  
3.0                              0.429153           0.0     -3.249285e-16  
4.0                              0.428788           0.0      3.363617e-17  
5.0                              0.428544           0.0     -3.973285e-16  
...                                   ...           ...               ...  
163835.0                         0.254179           0.0      1.373954e-03  
196603.0                         0.235487           0.0      1.576063e-03  
229371.0                         0.218393           0.0      1.764700e-03  
262139.0                         0.202687           0.0      1.941593e-03  
294907.0                         0.188225           0.0      2.107906e-03  

[79 rows x 6 columns]

In [210]:
columns = df.columns.to_list()
columns

['BHE active length',
 'Borehole radius',
 'Ground thermal conductivity',
 'Ground volumetric heat capacity',
 'BHE distance',
 'BHE buried depth']

In [211]:
dm.use_dmpl_style()
plt.rcParams['font.size'] = 9

targets = [
    'Ground volumetric heat capacity',
    'Ground thermal conductivity',
    'Borehole radius',
    'BHE distance',
]

name_dict = {
    'BHE active length' : '$L$ [m]',
    'Borehole radius' : '$r_b$ [cm]',
    'Ground thermal conductivity' : '$k_s$ [W/m $\cdot$ K]',
    'Ground volumetric heat capacity' : '$C_s$ [MJ]', #10^6 으로 나눠서 사용하시면 됩니다. 
    'BHE distance' : '$d$ [m]',
    'BHE buried depth' : '$D$ [m]'
}

base_color = 'indigo'

colors = {
    1 : f'dm.{base_color}3',
    2 : f'dm.{base_color}4',
    4 : f'dm.{base_color}6',
    8 : f'dm.{base_color}7',
}

lstyles =  {
    1 : ':',
    2 : '-.',
    4 : '--',
    8 : '-',
}


fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(12)))

offset = dm.make_offset(5, -5, fig)
offset2 = dm.make_offset(15, -5.5, fig)

gs = fig.add_gridspec(
    2, 2, left=0.1, right=0.95, bottom=0.1, top=0.90, wspace=0.1, hspace=0.15,
)

axs = gs.subplots(sharex=True, sharey=True)

lines = []
for name, ax, abc in zip(targets, axs.flat, 'abcd'):
    for n in (1, 2, 4, 8):
        # if name == 'BHE distance' and n == 1:
        #     continue

        x = sa_data[n].index.to_numpy().astype(float)
        y = sa_data[n][name].to_numpy()

        line, = ax.plot(x, y, lw=0.7, c=colors[n], ls=lstyles[n])
        lines.append(line)
        
    ax.text(
        0, 1, f'{abc}', transform=ax.transAxes + offset, weight='bold',
        va='top', ha='left', fontsize=dm.fs(0),
    )

    ax.text(
        0, 1, f'{name} ({name_dict[name].split()[0]})', transform=ax.transAxes + offset2, weight='normal',
        va='top', ha='left', fontsize=dm.fs(-1),
    )

    if name == targets[1]:
        ax.legend(
            lines, [f'{n} $\\times$ {n}' for n in (1, 2, 4, 8)],
            # loc='lower right', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(1.02, 1.02),
            mode='expand', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(0, 1.07, 1, 0.105),
            columnspacing=2.5,
        )

        # if n == 2:
        #     ax.legend(
        #         lines[3:], [name_dict[name] for name in columns][3:],
        #         # loc='lower right', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(1.02, 1.02),
        #         mode='expand', ncols=6, fontsize=dm.fs(-1), bbox_to_anchor=(0, 1.07, 1, 0.105),
        #         columnspacing=2.5,
        #     )

for ax in axs.flat:
    ax.set_xlim(1, max_x)
    ax.set_ylim(-0.03, 1)
    # ax.set_xticks(np.arange(-18, 21, 4))
    ax.set_yticks(np.arange(0, 1.1, 0.5))
    ax.set_xscale('log')
    
for ax in axs[:, 0]:
    # ax.set_ylabel('First-order sensitivity index [-]')
    ax.set_ylabel('')

fig.text(0.025, 0.5, 'First-order sensitivity index [-]', va='center', rotation='vertical')

for ax in axs[1, :]:
    ax.set_xlabel('Time [h]')

dm.save_and_show(fig, size=800)

In [212]:
dm.save_formats(fig, './figure/Fig. 5 Transient variation of the first order sensitivity index of influential parameters on g-function')

# Figure 6. total heat exchange rate for 8760 hours and peak load period of cooling and heating

In [213]:
df = pd.read_csv('./data/fig6/synthetic_load.csv')
df['y'] /= 1e3

df

x         y
0        0  0.000160
1        1  0.000160
2        2  0.000160
3        3  0.000160
4        4  0.000160
...    ...       ...
8756  8756  0.035931
8757  8757  1.837282
8758  8758  4.094258
8759  8759  6.242094
8760  8760  7.808902

[8761 rows x 2 columns]

In [214]:
dm.use_dmpl_style()
plt.rcParams['font.size'] = 8

# (a)와 그 옆의 타이틀 폰트사이즈가 다른데 같게할지 정해야 함.
abc_n = 0
title_n = -1

fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(10)))

offset = dm.make_offset(3, -3, fig)
offset2 = dm.make_offset(12, -3 + 0.5 * title_n, fig)

gs = fig.add_gridspec(
    2, 2, left=0.1, right=0.95, bottom=0.1, top=0.95, wspace=0.4, hspace=0.5,
)

axs = []

# Subplot a.
ax = fig.add_subplot(gs[0, :])
axs.append(ax)

ax.set_xticks(np.arange(0, 8761, 1000).tolist() + [8760])
# ax.set_xticks(np.arange(0, 8761, 876).tolist())
ax.set_xlim(0, 8760)

ax.text(
    0, 1, f'a', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

ax.text(
    0, 1, f'Total heat exchange rate profile', transform=ax.transAxes + offset2, weight='normal',
    va='top', ha='left', fontsize=dm.fs(title_n), zorder=1000,
)

# Subplot b.
ax = fig.add_subplot(gs[1, 0])
axs.append(ax)

ax.set_xlim(4272, 4440)

ax.text(
    0, 1, f'b', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

ax.text(
    0, 1, f'Peak cooling heat rate profile for 168 hours', transform=ax.transAxes + offset2, weight='normal',
    va='top', ha='left', fontsize=dm.fs(title_n), zorder=1000,
)

# Subplot c.
ax = fig.add_subplot(gs[1, 1])
axs.append(ax)

ax.set_xlim(8592, 8760)

ax.text(
    0, 1, f'c', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

ax.text(
    0, 1, f'Peak heating heat rate profile for 168 hours', transform=ax.transAxes + offset2, weight='normal',
    va='top', ha='left', fontsize=dm.fs(title_n), zorder=1000,
)

axs = np.array(axs)
for i, ax in enumerate(axs):
    if i == 0:
        lw = 0.3
        alpha=0.1
    else:
        lw = 0.8
        alpha=0.05

    ax.plot(df['x'][:2200], df['y'][:2200], lw=lw, c='dm.red6')
    ax.plot(df['x'][2200:6600], df['y'][2200:6600], lw=lw, c='dm.blue6')
    ax.plot(df['x'][6600:], df['y'][6600:], lw=lw, c='dm.red6')
    ax.fill_between([4272, 4440], [-220, -220], [220, 220], fc='dm.blue5', alpha=alpha, lw=0, zorder=100)
    ax.fill_between([8592, 8760], [-220, -220], [220, 220],  fc='dm.red5', alpha=alpha, lw=0, zorder=100)

    ax.set_ylim(-220, 220)
    ax.set_xlabel('Time [h]')
    ax.set_ylabel('Heat rate [kW]')

fig.align_ylabels(axs[:2])

dm.save_and_show(fig)

In [215]:
dm.save_formats(fig, './figure/Fig. 6 total heat exchange rate for 8760 hours and peak load period of cooling and heating')

The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.


# Figure 7. Variation of outlet fluid temperature of BHE throughout 8760 hours and during peak time

In [216]:
# df = pd.read_csv('./data/fig7/4x4.csv')
# df.drop(columns=['Unnamed: 0'], inplace=True)

# x = df.columns.to_numpy().astype(float).astype(int)
# quantiles = np.quantile(df.values, [0, 0.025, 0.5, 0.975, 1.0], axis=0)

# # Find distribution at minimum position.
# i = np.argmin(quantiles[1][72:240])
# print(x[72:240][i])

# data1 = df.values[:, 72:240][:, i]

# # Find maximum position.
# i = np.argmax(quantiles[1][4440:4608])
# print(x[4440:4608][i])

# data2 = df.values[:, 4440:4608][:, i]

# # Save data to be visualized in the next figure.
# np.savetxt('./data/fig7/x.csv', x, delimiter=',')
# np.savetxt('./data/fig7/data1.csv', data1, delimiter=',')
# np.savetxt('./data/fig7/data2.csv', data2, delimiter=',')
# np.savetxt('./data/fig7/quantiles.csv', quantiles, delimiter=',')

In [217]:
# Load data to be visualized in the next figure.
x = np.loadtxt('./data/fig7/x.csv', delimiter=',')
data1 = np.loadtxt('./data/fig7/data1.csv', delimiter=',')
data2 = np.loadtxt('./data/fig7/data2.csv', delimiter=',')
quantiles = np.loadtxt('./data/fig7/quantiles.csv', delimiter=',')

# CI 95%.
# quantiles = quantiles[1:-1]

# Full CI.
quantiles = quantiles[[0, 2, 4]]

data1_x = np.linspace(-3, 3, 1000)
data1_y = gaussian_kde(data1)(data1_x)

data2_x = np.linspace(29, 35, 1000)
data2_y = gaussian_kde(data2)(data2_x)

In [218]:
dm.use_dmpl_style()
plt.rcParams['font.size'] = 8

range_info = {
    'a': {
        'xlim': (0, 8760),
        'xticks': (0, 1000, 2000, 3000, 4000, 5000, 6000, 7000, 8000),
        'xticklabels': None,
        'ylim': (-5, 45),
        'yticks': (-5, 5, 15, 25, 35, 45),
        'yticklabels': None,
    },
    'b': {
        'xlim': (72, 240),
        'xticks': None,
        'xticklabels': None,
        'ylim': (-5, 25),
        'yticks': np.arange(-5, 26, 10),
        'yticklabels': None,
    },
    'c': {
        'xlim': (4440, 4608),
        'xticks': None,
        'xticklabels': None,
        'ylim': (15, 45),
        'yticks': np.arange(15, 46, 10),
        'yticklabels': None,
    },
    'd': {
        'xlim': (-3, 3),
        'xticks': np.arange(-3, 3.5, 1),
        'xticklabels': None,
        'ylim': (0, 1),
        'yticks': (0, 0.5, 1),
        'yticklabels': None,
    },
    'e': {
        'xlim': (29, 35),
        'xticks': np.arange(29, 35.5, 1),
        'xticklabels': None,
        'ylim': (0, 1),
        'yticks': (0, 0.5, 1),
        'yticklabels': None,
    }
}

fill_colors = {
    'a': {
        'low': 'dm.red5',
        'high': 'dm.blue5',
    },
    'b': {
        'low': 'dm.red5',
        'high': 'dm.blue5',
    },
    'c': {
        'low': 'dm.red5',
        'high': 'dm.blue5',
    },
    'd': 'dm.red5',
    'e': 'dm.blue5',
}

# Font sizes.
abc_n = 0
title_n = -1
label_n = 0
legend_n = -1

fig = plt.figure(figsize=(dm.cm2in(17), dm.cm2in(15)))

offset = dm.make_offset(3, -3, fig)
offset2 = dm.make_offset(12, -3 + 0.5 * title_n, fig)

gs = fig.add_gridspec(
    3, 2, left=0.1, right=0.95, bottom=0.1, top=0.95, wspace=0.4, hspace=0.5,
)

axs = []

# Subplot a.
ax = fig.add_subplot(gs[0, :])
axs.append(ax)

ax.set_xlabel('Time [h]', fontsize=dm.fs(label_n))
ax.set_ylabel('Entering fuild temperature [$^{\circ}$C]', fontsize=dm.fs(label_n))

ax.text(
    0, 1, f'a', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

# Subplot b.
ax = fig.add_subplot(gs[1, 0])
axs.append(ax)

line, = ax.plot(x, quantiles[1], lw=0.3, c='dm.gray5')
fill = ax.fill_between(x, quantiles[0], quantiles[2], color='dm.gray5', alpha=0.3, lw=0)

ax.set_xlabel('Time [h]', fontsize=dm.fs(-1))
ax.set_ylabel('Entering fuild temperature [$^{\circ}$C]', fontsize=dm.fs(label_n))

ax.text(
    0, 1, f'b', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

# Subplot c.
ax = fig.add_subplot(gs[1, 1])
axs.append(ax)

line, = ax.plot(x, quantiles[1], lw=0.3, c='dm.gray5')
fill = ax.fill_between(x, quantiles[0], quantiles[2], color='dm.gray5', alpha=0.3, lw=0)

ax.set_xlabel('Time [h]', fontsize=dm.fs(label_n))
ax.set_ylabel('Entering fuild temperature [$^{\circ}$C]', fontsize=dm.fs(label_n))

ax.text(
    0, 1, 'c', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

# Subplot d.
ax = fig.add_subplot(gs[2, 0])
axs.append(ax)

ax.set_xlabel('Entering fuild temperature [$^{\circ}$C]', fontsize=dm.fs(label_n))
ax.set_ylabel('Probability density', fontsize=dm.fs(label_n))

ax.text(
    0, 1, 'd', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

# Subplot e.
ax = fig.add_subplot(gs[2, 1])
axs.append(ax)

ax.set_xlabel('Entering fuild temperature [$^{\circ}$C]', fontsize=dm.fs(label_n))
ax.set_ylabel('Probability density', fontsize=dm.fs(label_n))

ax.text(
    0, 1, 'e', transform=ax.transAxes + offset, weight='bold',
    va='top', ha='left', fontsize=dm.fs(abc_n), zorder=1000,
)

axs = np.array(axs)
for i, (abc, ax) in enumerate(zip('abc', axs[:3])):
    if i == 0:
        lw = 0.3
        alpha=0.1
    else:
        lw = 0.7
        alpha=0.05

    line, = ax.plot(x, quantiles[1], lw=lw, c='dm.gray5')
    fill = ax.fill_between(x, quantiles[0], quantiles[2], color='dm.gray4', alpha=0.3, lw=0)

    if i == 0:
        ax.legend([line, fill], ['Median', 'Uncertainty range'], loc='upper right', fontsize=dm.fs(legend_n))

    ax.fill_between([72, 240], [-5, -5], [45, 45], fc=fill_colors[abc]['low'], alpha=alpha, lw=0, zorder=100)
    ax.fill_between([4440, 4608], [-5, -5], [45, 45],  fc=fill_colors[abc]['high'], alpha=alpha, lw=0, zorder=100)

    if i == 1:
        ax.axvline(157, c=fill_colors[abc]['low'], lw=0.5, ls=':')

    if i == 2:
        ax.axvline(4525, c=fill_colors[abc]['high'], lw=0.5, ls=':')


ax = axs[3]
ax.fill(data1_x, data1_y, fc=fill_colors['d'], alpha=0.4, lw=0)
# ax.plot(data1_x, data1_y, c=fill_colors['d'], alpha=1, lw=0.2)

ax = axs[4]
ax.fill(data2_x, data2_y, fc=fill_colors['e'], alpha=0.4, lw=0)


for abc, ax in zip('abcde', axs):
    print(abc)

    if range_info[abc]['xlim'] is not None:
        ax.set_xlim(range_info[abc]['xlim'])

    if range_info[abc]['xticks'] is not None:
        ax.set_xticks(range_info[abc]['xticks'])

    if range_info[abc]['xticklabels'] is not None:
        ax.set_xticklabels(range_info[abc]['xticklabels'])

    if range_info[abc]['ylim'] is not None:
        ax.set_ylim(range_info[abc]['ylim'])

    if range_info[abc]['yticks'] is not None:
        ax.set_yticks(range_info[abc]['yticks'])

    if range_info[abc]['yticklabels'] is not None:
        ax.set_yticklabels(range_info[abc]['yticklabels'])

# for i, ax in enumerate(axs):
#     if i == 0:
#         lw = 0.3
#         alpha=0.1
#     else:
#         lw = 0.8
#         alpha=0.05

#     # ax.plot(df['x'][:2200], df['y'][:2200], lw=lw, c='dm.red6')
#     # ax.plot(df['x'][2200:6600], df['y'][2200:6600], lw=lw, c='dm.blue6')
#     # ax.plot(df['x'][6600:], df['y'][6600:], lw=lw, c='dm.red6')
#     # ax.fill_between([4272, 4440], [-220, -220], [220, 220], fc='dm.blue5', alpha=alpha, lw=0, zorder=100)
#     # ax.fill_between([8592, 8760], [-220, -220], [220, 220],  fc='dm.red5', alpha=alpha, lw=0, zorder=100)

#     ax.set_ylim(-220, 220)
#     ax.set_xlabel('Time [h]')
#     ax.set_ylabel('Heat rate [kW]')

fig.align_ylabels(axs[:2])

dm.save_and_show(fig, size=800)

a
b
c
d
e


In [219]:
dm.save_formats(fig, './figure/Fig. 7 Variation of outlet fluid temperature of BHE throughout 8760 hours and during peak time')

The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.


# Figure 8. Variation of OFT probability density function due to reduced parameter uncertainty

In [220]:
# with open('./data/fig8/C.csv', 'r') as f:
#     x = np.array([float(v) for v in f.readline().split(',')[1:]])
#     y = np.array([float(v) for v in f.readline().split(',')[1:]])

# print(np.argmin(y))
# print(x[np.argmin(y)])

In [221]:
# data_dict = {
#     'all': pd.read_csv('./data/fig8/all.csv', usecols=[8725]).values,
#     'C': pd.read_csv('./data/fig8/C.csv', usecols=[8725]).values,
#     'd': pd.read_csv('./data/fig8/d.csv', usecols=[8725]).values,
#     'ks': pd.read_csv('./data/fig8/ks.csv', usecols=[8725]).values,
#     'original': pd.read_csv('./data/fig8/original.csv', usecols=[8725]).values,
#     'rb': pd.read_csv('./data/fig8/rb.csv', usecols=[8725]).values,
# }

# df = pd.DataFrame({k: v.flatten() for k, v in data_dict.items()})
# df.to_csv('./data/fig8/pdf.csv')

In [222]:
df = pd.read_csv('./data/fig8/pdf.csv', index_col=0)
df

all         C         d        ks  original        rb
0    -0.205098 -0.283430 -0.293529 -0.263680 -0.292504 -0.243237
1    -0.187086 -0.265264 -0.275416 -0.245496 -0.274341 -0.225194
2    -0.267082 -0.371473 -0.381600 -0.352884 -0.380515 -0.304565
3    -0.095579 -0.043688 -0.053650 -0.159909 -0.052466  0.008651
4    -0.116827 -0.195587 -0.085798 -0.056900 -0.084937 -0.034231
...        ...       ...       ...       ...       ...       ...
9795 -0.227008 -0.486554 -0.381495 -0.200543 -0.388669 -0.338855
9796  0.115708  0.426725  0.191704 -0.258431  0.176856  0.295659
9797  0.458945  0.765800  0.844047  0.448621  0.846709  0.969446
9798  0.447931  0.739826  0.832542  0.426603  0.822212  0.944948
9799  0.447369  0.739264  0.831999  0.426041  0.821661  0.944400

[9800 rows x 6 columns]

In [223]:
# # Write cols in reverse order.
# cols = ['all', 'ks', 'C', 'd', 'rb', 'original']

cols = ['original', 'rb', 'd', 'C', 'ks', 'all']

colors = [
    f'dm.red{i}' for i in range(7, 1, -1)
][::-1]

name_dict = {
    'original' : 'Original',
    'rb' : '$r_b$',
    'ks' : '$k_s$',
    'C' : '$C_s$', #10^6 으로 나눠서 사용하시면 됩니다. 
    # d or D?
    'd' : '$d$',
    'all' : 'All'
}

x = np.linspace(-2.5, 2, 100)
y_dict = {
    k: gaussian_kde(df[k])(x) for k in cols
}

In [224]:
fig = plt.figure(figsize=(dm.cm2in(9), dm.cm2in(7)))

# hspace로 ridge plot 간격 설정할 수 있음.
gs = fig.add_gridspec(
    6, 1, left=0.1, right=0.85, bottom=0.15, top=0.95, hspace=-0.5,
)

axs = gs.subplots(sharex=True)

for i, ax in enumerate(axs.flat):
    name = cols[i]
    color = colors[i]

    ax.fill_between(x, y_dict[name], fc=color, alpha=1, lw=0.4, ec='white')
    # ax.plot([0, 1], [0, 1], zorder=100+i, clip_on=False)
    ax.grid(False)

    # Last subplot (bottom).
    if i == 5:
        ax.set_xlabel('Entering fluid temperature in heating peak [$^{\circ}$C]')
        ax.set_xlim(-2.6, 1.6)
        ax.set_xticks(np.arange(-2.5, 1.6, 1))
        # X축 tick size. 0도 괜찮을 것 같음 (정량적인 것보다는 상대적 넓이가 중요하기 때문에).
        ax.xaxis.set_tick_params(which='major', size=0)
    
    if i != 5:
        ax.spines['bottom'].set(linewidth=0.5, color='dm.gray3')
        # Remove minior ticks.
        ax.xaxis.set_tick_params(which='both', bottom=False)
        # ax.yaxis.set_tick_params(which='both', bottom=False)
    
    ax.xaxis.set_tick_params(which='minor', bottom=False)
    ax.set_yticks([])

    ax.patch.set_alpha(0.0)
    ax.spines['left'].set_visible(False)
    ax.spines['right'].set_visible(False)
    ax.spines['top'].set_visible(False)
    
    # Text 배치가 달라지면 grid spec도 수정해야 함.

    # 오른쪽에 배치.
    offset = dm.make_offset(7, 0, fig)
    ax.text(1, 0, name_dict[name], transform=ax.transAxes + offset, weight='normal', va='center', ha='left', fontsize=dm.fs(-2))
    # 왼쪽에 배치.
    # offset = dm.make_offset(-5, 0, fig)
    # ax.text(0, 0, name_dict[name], transform=ax.transAxes + offset, weight='normal', va='center', ha='right', fontsize=dm.fs(-2))

fig.text(0.03, 0.55, 'Probability density', va='center', rotation='vertical')

dm.save_and_show(fig)

In [225]:
dm.save_formats(fig, './figure/Fig. 8 Variation of OFT probability density function due to reduced parameter uncertainty')